# Awesum Care dataset upload flow.

### This section describe the flow for turning information from text to vector for RAG. The vector db used below is locally hosted. To upload to the production, change the qdrant config.

1. Put the data into a text file (.pdf/.docx/.txt/.md), then put then into a subdirectory. (/awesumcare_data in this example).
2. Change them to embedding.
3. Verify locally if works.

(If without old data file)

4. Create a duplicate of existing collection.
5. Deploy new collection with snapshots and upload new data

### Read the data

In [1]:
from llama_index.core import SimpleDirectoryReader

from custom_io import MarkdownReader, UnstructuredReader, default_file_metadata_func

dir_reader = SimpleDirectoryReader(
    "./awesumcare_data",
    file_extractor={
        ".pdf": UnstructuredReader(),
        ".docx": UnstructuredReader(),
        ".pptx": UnstructuredReader(),
        ".md": MarkdownReader(),
    },
    recursive=True,
    exclude=["*.png", "*.pptx", "*.docx", "*.pdf"],
    file_metadata=default_file_metadata_func,
)

documents = dir_reader.load_data()

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\josh\AppData\Roaming\nltk_data...
[n

Create the embedding client add feed to the IngestionPipeline

In [ ]:
from llama_index.core import VectorStoreIndex
from llama_index.core.ingestion import IngestionPipeline
from llama_index.embeddings.azure_openai import AzureOpenAIEmbedding
from llama_index.vector_stores.qdrant import QdrantVectorStore


import qdrant_client
import nest_asyncio

client = qdrant_client.QdrantClient(location=":memory:")
vector_store = QdrantVectorStore(client=client, collection_name="test_store")

embedding_client = AzureOpenAIEmbedding(
    deployment_name="text-embedding-ada-002",
    api_key="",
    azure_endpoint="",
    api_version="2024-02-01",
)

pipeline = IngestionPipeline(
    transformations=[
        embedding_client,
    ],
    vector_store=vector_store,
)

# Need this for the code to run in my jupyter notebook. Not sure if needed in a different env.
nest_asyncio.apply()

# Ingest directly into a vector db
pipeline.run(documents=documents)

# Create your index
index = VectorStoreIndex.from_vector_store(
    vector_store=vector_store, embed_model=embedding_client
)

Verify embeeding result:

In [3]:
from qdrant_client.http import models
import random

# You can comment out this line to reuse the same query vector after a run if you find the results unsatisfactory.
# This allows you to compare the results after modify the document.
query_vector=[random.random() for _ in range(1536)]

res = client.search(
    collection_name="test_store",
    search_params=models.SearchParams(hnsw_ef=128, exact=False),
    # create a list of random float with 1536 elements
    query_vector=query_vector,
    limit=3,
)

# Need this line, or will have error: "NameError: name 'null' is not defined"
null = None
print(eval(res[0].payload["_node_content"])["text"])
print(eval(res[1].payload["_node_content"])["text"])
print(eval(res[2].payload["_node_content"])["text"])

7. 見證人可以是親人嗎？

    見證人不能是遺囑的受益人或受益人的配偶。如果親人是遺囑的見證人，那他們便不能在遺囑中有利益關係，意思是親人不能同時作為遺囑的見證人及受益人。見證人必須是年滿18歲且具有完全行為能力的成年人。
18. 在遺囑裡分配共同擁有一物業（長命契），”如何分配所持有的物業”一欄應如何填寫？

    在填寫遺囑時，如果涉及共同擁有的物業（例如長命契），需要特別注意如何分配這部分資產。共同擁有的物業通常有兩種形式：聯權共有（長命契）和分權共有（分權契）。
    ### 聯權共有（長命契）：
    > - 在聯權共有的情況下，當其中一位擁有人去世，其持有的份額會自動轉移給其他聯權共有人，這稱為「生者繼承權」。這種情況下，該物業的份額通常不會在遺囑中分配，因為它自動轉移給其他共有人。
    ### 分權共有（分權契）：
    > - 在分權共有的情況下，每位共有人擁有物業的特定份額，並且這些份額可以在遺囑中分配給指定的受益人。
    > - 在填寫遺囑的「如何分配所持有的物業」一欄時，可以就分權共有的物業分配，寫上：我所持有的 [物業地址] 的 [百分比或具體份額]，應分配給 [受益人姓名]。
8. 遺囑一定需要見證人嗎？沒有見證人的遺囑有效嗎？

    是的，遺囑必須有見證人。根據《遺囑條例》（第30章）第5(1)(c)條，一份具有法律效力的遺囑必須在兩名年滿18歲且非受益人的獨立見證人面前簽署和加上日期。如果遺囑沒有見證人，則該遺囑可能會被視為無效。請注意，如果立遺囑人年紀較大，或已開始有腦退化症狀，最好找醫生見證。此外，如果遺產承辦處對非律師製作的遺囑的真實性有任何疑問，可能會要求見證人簽署並作出有關見證遺囑的聲明。
